## Run this notebook

You can launch this notbook using mybinder, by clicking the button below.

<a href="https://mybinder.org/v2/gh/NASA-IMPACT/veda-docs/HEAD?labpath=notebooks/quickstarts%2Fwfs.ipynb">
<img src="https://mybinder.org/badge_logo.svg" alt="Binder" title="A cute binder" width="150"/> 
</a>

## Approach

   1. Use `OWSLib` to determine what data is available and inspect the metadata
   2. Use `OWSLib` to filter and read the data
   3. Use `geopandas` and `folium` to analyze and plot the data

Note that the default examples environment is missing one requirement: `oswlib`. We can `pip install` that before we move on. 

In [1]:
!pip install OWSLib==0.28.1

You should consider upgrading via the '/opt/conda/bin/python3.7 -m pip install --upgrade pip' command.


In [2]:
from owslib.ogcapi.features import Features
import geopandas as gpd
import datetime as dt
from datetime import datetime, timedelta

## About the Data


The fire data shown is generated by the FEDs algorithm. The FEDs algorithm tracks fire movement and severity by ingesting observations from the VIIRS thermal sensors on the Suomi NPP and NOAA-20 satellites. This algorithm uses raw VIIRS observations to generate a polygon of the fire, locations of the active fire line, and estimates of fire mean Fire Radiative Power (FRP). The VIIRS sensors overpass at ~1:30 AM and PM local time, and provide estimates of fire evolution ~ every 12 hours. The data produced by this algorithm describe where fires are in space and how fires evolve through time. This CONUS-wide implementation of the FEDs algorithm is based on [Chen et al 2020’s](https://www.nature.com/articles/s41597-022-01343-0) algorithm for California.


The data produced by this algorithm is considered experimental. 

## Look at the data that is availible through the OGC API

The datasets that are distributed throught the OGC API are organized into collections.
We can display the collections with the command: 

In [3]:
OGC_URL = "https://firenrt.delta-backend.com"

w = Features(url=OGC_URL)
w.feature_collections()

['public.eis_fire_lf_nfplist_nrt',
 'public.eis_fire_snapshot_newfirepix_nrt',
 'public.eis_fire_newfirepix',
 'public.eis_fire_lf_fireline_nrt',
 'public.eis_fire_lf_perimeter_archive',
 'public.eis_fire_lf_fireline_archive',
 'public.eis_fire_fireline',
 'public.eis_fire_lf_newfirepix_archive',
 'public.eis_fire_perimeter',
 'public.eis_fire_lf_nfplist_archive',
 'public.eis_fire_snapshot_perimeter_nrt',
 'public.eis_fire_snapshot_fireline_nrt',
 'public.eis_fire_lf_perimeter_nrt',
 'public.eis_fire_lf_newfirepix_nrt',
 'public.st_squaregrid',
 'public.st_hexagongrid',
 'public.st_subdivide']

We will focus on the `public.eis_fire_snapshot_fireline_nrt` collection, the `public.eis_fire_snapshot_perimeter_nrt` collection, and the `public.eis_fire_lf_perimeter_archive` collection here. 

### Inspect the metatdata for public.eis_fire_snapshot_perimeter_nrt collection

We can access information that describes the `public.eis_fire_snapshot_perimeter_nrt` table. 

In [4]:
perm = w.collection("public.eis_fire_snapshot_perimeter_nrt")

We are particularly interested in the spatial and temporal extents of the data.

In [5]:
perm["extent"]

{'spatial': {'bbox': [[-124.61687469482422,
    24.069549560546875,
    -63.63948059082031,
    49.40034866333008]],
  'crs': 'http://www.opengis.net/def/crs/OGC/1.3/CRS84'},
 'temporal': {'interval': [['2023-05-03T00:00:00+00:00',
    '2023-05-23T00:00:00+00:00']],
  'trs': 'http://www.opengis.net/def/uom/ISO-8601/0/Gregorian'}}

In addition to getting metadata about the data we can access the queryable fields. Each of these fields will represent a column in our dataframe.

In [6]:
perm_q = w.collection_queryables("public.eis_fire_snapshot_perimeter_nrt")
perm_q["properties"]

{'wkb_geometry': {'$ref': 'https://geojson.org/schema/Geometry.json'},
 'duration': {'name': 'duration', 'type': 'number'},
 'farea': {'name': 'farea', 'type': 'number'},
 'fireid': {'name': 'fireid', 'type': 'number'},
 'flinelen': {'name': 'flinelen', 'type': 'number'},
 'fperim': {'name': 'fperim', 'type': 'number'},
 'isactive': {'name': 'isactive', 'type': 'number'},
 'meanfrp': {'name': 'meanfrp', 'type': 'number'},
 'n_newpixels': {'name': 'n_newpixels', 'type': 'number'},
 'n_pixels': {'name': 'n_pixels', 'type': 'number'},
 'ogc_fid': {'name': 'ogc_fid', 'type': 'number'},
 'pixden': {'name': 'pixden', 'type': 'number'},
 't': {'name': 't', 'type': 'string'}}

## Filter the data

It is always a good idea to do any data filtering as early as possible. In this example we know that we want the data for particular spatial and temporal extents. We can apply those and other filters using the `OWSLib` package.

In the below example we are:

 - choosing the `public.eis_fire_snapshot_perimeter_nrt` collection 
 - subsetting it by space using the `bbox` parameter
 - subsetting it by time using the `datetime` parameter
 - filtering for fires over 5km^2 and over 2 days long using the `filter` parameter. The `filter` parameter lets us filter by the columns in 'public.eis_fire_snapshot_perimeter_nrt' using SQL-style queries. 

NOTE: The `limit` parameter desginates the maximum number of objects the query will return. The default limit is 10, so if we want to all of the fire perimeters within certain conditions, we need to make sure that the limit is large.

In [7]:
## Get the most recent fire perimeters, and 7 days before most recent fire perimeter
most_recent_time = max(*perm["extent"]["temporal"]["interval"])
now = dt.datetime.strptime(most_recent_time, "%Y-%m-%dT%H:%M:%S+00:00")
last_week = now - dt.timedelta(weeks=1)
last_week = dt.datetime.strftime(last_week, "%Y-%m-%dT%H:%M:%S+00:00")
print("Most Recent Time =", most_recent_time)
print("Last week =", last_week)

Most Recent Time = 2023-05-23T00:00:00+00:00
Last week = 2023-05-16T00:00:00+00:00


In [8]:
perm_results = w.collection_items(
    "public.eis_fire_snapshot_perimeter_nrt",  # name of the dataset we want
    bbox=["-106.8", "24.5", "-72.9", "37.3"],  # coodrinates of bounding box,
    datetime=[last_week + "/" + most_recent_time],  # date range
    limit=1000,  # max number of items returned
    filter="farea>5 AND duration>2",  # additional filters based on queryable fields
)

The result is a dictionary containing all of the data and some summary fields. We can look at the keys to see what all is in there.

In [9]:
perm_results.keys()

dict_keys(['type', 'id', 'title', 'description', 'numberMatched', 'numberReturned', 'links', 'features'])

For instance you can check the total number of matched items and make sure that it is equal to the number of returned items. This is how you know that the `limit` you defined above is high enough.

In [10]:
perm_results["numberMatched"] == perm_results["numberReturned"]

True

You can also access the data directly in the browser or in an HTTP GET call using the constructed link.

In [11]:
perm_results["links"][1]["href"]

'https://firenrt.delta-backend.com/collections/public.eis_fire_snapshot_perimeter_nrt/items?bbox=-106.8%2C24.5%2C-72.9%2C37.3&datetime=2023-05-16T00%3A00%3A00%2B00%3A00%2F2023-05-23T00%3A00%3A00%2B00%3A00&limit=1000&filter=farea%3E5+AND+duration%3E2'

## Read data

In addition to all the summary fields, the `perm_results` dict contains all the data. We can pass the data into geopandas to make it easier to interact with.

In [12]:
df = gpd.GeoDataFrame.from_features(perm_results["features"])
df

geometry  duration       farea  \
0  POLYGON ((-78.05380 25.07529, -78.05382 25.075...       8.5    6.787331   
1  POLYGON ((-81.06449 25.95495, -81.06448 25.954...      16.5   81.413491   
2  POLYGON ((-81.66818 29.24672, -81.66808 29.246...       4.0    7.789717   
3  POLYGON ((-85.52621 30.03404, -85.52414 30.037...       8.0   12.906472   
4  MULTIPOLYGON (((-84.18103 30.73800, -84.18102 ...      80.5  594.630290   
5  MULTIPOLYGON (((-103.52577 32.22440, -103.5257...      17.0   10.940001   
6  POLYGON ((-104.08174 32.22901, -104.08175 32.2...      11.0   15.296388   
7  POLYGON ((-106.30889 25.15346, -106.30888 25.1...       6.0    7.757181   
8  POLYGON ((-106.30553 24.99012, -106.30554 24.9...       8.5   16.009259   

   fireid  flinelen      fperim  isactive  meanfrp  n_newpixels  n_pixels  \
0   63349       0.0   10.125732         1      0.0            0        32   
1   59462       0.0   37.958965         1      0.0            0       544   
2   65940       0.0   12.359742         1      0.0            0        66   
3   64561       0.0   17.488802         1      0.0            0       127   
4   23106       0.0  391.297316         1      0.0            0      1553   
5   61561       0.0   19.953733         1      0.0            0        22   
6   62322       0.0   17.629951         1      0.0            0         8   
7   63955       0.0   11.384919         1      0.0            0        92   
8   62262       0.0   19.050446         0      0.0            0       144   

   ogc_fid     pixden                    t  
0        2   4.714666  2023-05-19T00:00:00  
1       21   6.681939  2023-05-18T12:00:00  
2      180   8.472709  2023-05-21T12:00:00  
3      585   9.840024  2023-05-22T12:00:00  
4     2307   2.611707  2023-05-21T00:00:00  
5     6756   2.010969  2023-05-22T00:00:00  
6     6802   0.522999  2023-05-19T00:00:00  
7     7851  11.859979  2023-05-18T12:00:00  
8     7862   8.994795  2023-05-16T00:00:00

## Explore data

We can quickly explore the data by setting the coordinate reference system (`crs`) and using `.explore()`

In [13]:
df = df.set_crs("EPSG:4326")
df.explore()

## Visualize Most Recent Fire Perimeters with Firelines

If we wanted to combine collections to make more informative analyses, we can use some of the same principles. 

First we'll get the queryable fields, and the extents:

In [14]:
fline_q = w.collection_queryables("public.eis_fire_snapshot_fireline_nrt")
fline_collection = w.collection("public.eis_fire_snapshot_fireline_nrt")
fline_q["properties"]

{'wkb_geometry': {'$ref': 'https://geojson.org/schema/Geometry.json'},
 'fireid': {'name': 'fireid', 'type': 'number'},
 'mergeid': {'name': 'mergeid', 'type': 'number'},
 'ogc_fid': {'name': 'ogc_fid', 'type': 'number'},
 't': {'name': 't', 'type': 'string'}}

### Read
Then we'll use those fields to get most recent fire perimeters and fire lines.

In [15]:
perm_results = w.collection_items(
    "public.eis_fire_snapshot_perimeter_nrt",
    datetime=most_recent_time,
    limit=1000,
)
perimeters = gpd.GeoDataFrame.from_features(perm_results["features"])

## Get the most recent fire lines
perimeter_ids = perimeters.fireid.unique()
perimeter_ids = ",".join(map(str, perimeter_ids))

fline_results = w.collection_items(
    "public.eis_fire_snapshot_fireline_nrt",
    limit=1000,
    filter="fireid IN ("
    + perimeter_ids
    + ")",  # only the fires from the fire perimeter query above
)
fline = gpd.GeoDataFrame.from_features(fline_results["features"])

### Visualize

In [16]:
perimeters = perimeters.set_crs("epsg:4326")
fline = fline.set_crs("epsg:4326")

m = perimeters.explore()
m = fline.explore(m=m, color="orange")
m

## Visualize the Growth of the Camp Fire

We may be interested in understanding how a fire evolved through time. To do this, we can work with the "Large fire" or "lf" perimeter collections. The `public.eis_fire_lf_perimeter_nrt` colelction has the full spread history of fires from this year. `public.eis_fire_lf_perimeter_archive` has the full spread history of fires from 2018-2021 that were in the Western United States. The Camp Fire was in 2018, so we will work with the `public.eis_fire_lf_perimeter_archive` collection. 

We can start by querying with information specific to the Camp Fire, like it's genreal region (Northern California), and when it was active (November 2018). 

In [17]:
perimeters_archive_results = w.collection_items(
    "public.eis_fire_lf_perimeter_archive",  
    bbox=["-124.52", "39.2", "-120", "42"],  # North California bounding box,
    datetime=["2018-11-01T00:00:00+00:00/2018-11-30T12:00:00+00:00"], 
    limit=3000, 
    filter="duration>2",  # additional filters based on queryable fields
)

perimeters_archive_results

perimeters = gpd.GeoDataFrame.from_features(perimeters_archive_results["features"])
perimeters = perimeters.sort_values(by = "t", ascending = False)
perimeters = perimeters.set_crs("epsg:4326")


m = perimeters.explore(style_kwds = {'fillOpacity':0})
m


## Download Data

Downloading pre-filtered data may be useful for working locally, or for working with the data in GIS software. 


We can download the dataframe we made by writing it out into a shapefile or into a GeoJSON file.  

    perimeters.to_file('perimeters.shp') 
    perimeters.to_file('perimeters.geojson', driver='GeoJSON')


## Collection Information

The API hosts 9 different collections. There are four different types of data, and three different time-scales availible for querying through the API. "\*snapshot\*" collections are useful for visualizing the most recent data. It contains the *most recent* fires perimeters, active firelines, or VIIRS observations within the last 20 days. "\*lf\*" collections (short for Large Fire), show *every* fire perimeter, active fire line, or VIIRS observations for fires *over 5 km^2*. Collections that end in \*archive are for year 2018 - 2021 across the Western United States. Collections with the \*nrt ending are for CONUS from this most recent year. FireIDs are consistent only between layers with the same timescale (*snapshot*, *lf_\*nrt*, and *lf\_*archive*). 



**public.eis_fire_snapshot_perimeter_nrt**

Perimeter of cumulative fire-area. Most recent perimeter from the last 20 days. 

**public.eis_fire_lf_perimeter_nrt**

Perimeter of cumulative fire-area, from fires over 5 km^2. Every fire perimeter from current year to date. 

**public.eis_fire_lf_perimeter_archive**

Perimeter of cumulative fire-area, from fires over 5 km^2 in the Western United States. Every fire perimeter from 2018-2021. 


| Column      | Description | Unit      |
| ----------- | ----------- | ----------- |
| meanfrp      | Mean fire radiative power. The weighted sum of the fire radiative power detected at each new pixel, divided by the number of pixels.   If no new pixels are detected, meanfrp is set to zero. | MW/(pixel area)  |
| t   | Time of  VIIRS detection, corrected to noon and midnight.   | Datetime. yyyy-mm-ddThh:mm:ss. Local time.  |
| fireid   | Fire ID. Unique for each fire. Matches fireid. |Numeric ID |
| pixden   |Number of pixels divided by area of perimeter.   | pixels/Km^2|
| duration  |Number of days since first observation of fire. Fires with a single observation have a duration of zero. |Days|
| flinelen   | Length of active fire line, based on new pixels. If no new pixels are detected, flinelen is set to zero.   |Km |
| fperim   | Length of fire perimeter.        | Km   |
| farea   | Area within fire perimeter.        |Km^2    |
| n_newpixels   | Number of pixels newly detected since last overpass.      |pixels  |
| n_pixels   | Number of pixel-detections in history of fire. | pixels   |
| isactive   | Have new fire pixels been detected in the last 5 days?     | Boolean |
| ogc_fid   |The ID used by the OGC API to sort perimeters.       | Numeric ID   |
| geometry  |The shape of the perimeter.    | Geometry    |


**public.eis_fire_snapshot_fireline_nrt**

Active fire line as estimated by new VIIRS detections. Most fire line from the last 20 days. 

**public.eis_fire_lf_fireline_nrt**

Active fire line as estimated by new VIIRS detections, from fires over 5 km^2. Every fire line from current year to date. 

**public.eis_fire_lf_fireline_nrt**

Active fire line as estimated by new VIIRS detections, from fires over 5 km^2 in the Western United States. Every fire line from 2018-2021. 

| Column      | Description | Unit      |
| ----------- | ----------- | ----------- |
| fireid   | ID of fire pixel associated with.      | Numeric ID |
| t   | Time of VIIRS detection, corrected to noon and midnight.| Datetime. yyyy-mm-ddThh:mm:ss. Local time.|
| mergeid  | ID used to connect pixels to perimeters. Matches fireid      | Numeric ID      |
| ogc_fid   |The ID used by the OGC API to sort pixels.      | Numeric ID     |

**public.eis_fire_snapshot_newfirepix_nrt**

New pixel detections that inform the most recent time-step’s perimeter and fireline calculation from the last 20 days.

**public.eis_fire_lf_newfirepix_nrt**

New pixel detections that inform a given time-step’s perimeter and fireline calculation. Availible from start of current year to date. 

**public.eis_fire_lf_newfirepix_archive**

New pixel detections that inform a given time-step’s perimeter and fireline calculation. Availible for Western United States from 2018-2021. 

| Column      | Description | Unit      |
| ----------- | ----------- | ----------- |
| fireid   | ID of fire pixel associated with.      | Numeric ID |
| t   | Time of VIIRS detection, corrected to noon and midnight. | Datetime. yyyy-mm-ddThh:mm:ss. Local time.|
| mergeid  | ID used to connect pixels to perimeters. Matches fireid      | Numeric ID      |
| ogc_fid   |The ID used by the OGC API to sort pixels.      | Numeric ID     |
